In [2]:
import tensorflow as tf
import librosa
import os
from IPython.display import display, Audio
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import argparse
from tensorflow.contrib import rnn

In [5]:
CONTENT_FILENAME = "neural-style-audio-tf/inputs/bach_violin.wav"
STYLE_FILENAME = "neural-style-audio-tf/inputs/elgar_cello.wav"

display(Audio(CONTENT_FILENAME))
display(Audio(STYLE_FILENAME))

In [6]:
# Reads wav file and produces spectrum
# Fourier phases are ignored
N_FFT = 2048
def read_audio_spectrum(filename):
    x, fs = librosa.load(filename)
    S = librosa.stft(x, N_FFT)
    p = np.angle(S)
    
    S = np.log1p(np.abs(S[:,:430]))  
    return S, fs



In [7]:
# get the spectograms for the content and style references
a_content, fs = read_audio_spectrum(CONTENT_FILENAME)
a_style, fs = read_audio_spectrum(STYLE_FILENAME)

N_SAMPLES = a_content.shape[1]
N_CHANNELS = a_content.shape[0]
a_style = a_style[:N_CHANNELS, :N_SAMPLES]

In [17]:
print np.shape(a_content)
print np.shape(a_style)
time_steps = N_CHANNELS # the time
num_hidden_units = 128 # the frequency
n_classes = 10 # not sure what this for - as outputs are usually probability layers
batch_size = 1
learning_rate = .001
n_input = N_SAMPLES
# maybe transpose the spectogram - at each timestemp, process each 'frequency layer'
a_content = np.transpose(a_content)
a_content = np.reshape(a_content, (1, time_steps, N_SAMPLES))
print np.shape(a_content)
a_style = np.transpose(a_style)



(430, 1025, 1)
(430, 1025)
(1, 1025, 430)


In [18]:
#weights and biases of appropriate shape to accomplish above task
out_weights=tf.Variable(tf.random_normal([num_hidden_units,n_classes]))
out_bias=tf.Variable(tf.random_normal([n_classes]))

#defining placeholders
#input image placeholder
x=tf.placeholder("float",[None, time_steps,n_input])
#input label placeholder
y=tf.placeholder("float",[None, n_classes])

# processing input tensor
input=tf.unstack(x ,time_steps,1)

In [20]:
lstm_layer=rnn.BasicLSTMCell(num_hidden_units,forget_bias=1)
outputs,_=rnn.static_rnn(lstm_layer,input,dtype="float32")
prediction=tf.matmul(outputs[-1],out_weights)+out_bias

In [21]:
print prediction

Tensor("add:0", shape=(?, 10), dtype=float32)
